<a href="https://colab.research.google.com/github/sukjin1/-/blob/main/sql_analysis_for_beginners_sample_v3.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 프로젝트 - 로컬팜 서비스 현황 분석 (Sample)

> **분석 대상 - 가상의 스타트업 로컬팜**

<img src="https://github.com/norusemari/img_store/blob/master/Localfarm_vision.png?raw=true" width=60%>

> **본문의 지도(Folium Map)와 그래프(Plotly)가 안보인다면?** 🔥🔥🔥🙏
- 상단의 **Open in Colab** 버튼을 클릭해주세요. 

> **샘플파일 확인간 참고 사항**

- 프로젝트는 가상의 스타트업 로컬팜 서비스에 대한 현황 분석을 진행합니다.
- **본 자료는 샘플자료로 실제 집계 쿼리(SQL)나, 시각화 코드(Plotly) 일부가 생략되어 있습니다.**


> **프로젝트 진행간 다루는 내용**

- **마케팅 데이터 분석**은 4주차 과정에서 기본지표(COST, LTV, ROAS) 집계 및 간단한 시각화 과정만 다루며 본 프로젝트에서는 다루지 않습니다.
- **engagement 분석**은 간단한 User Segment 방식을 활용해서 기본지표(AU, NRU, Retention) 를 집계하고 이를 통해 사용자 현황에 대해 분석합니다.
- **매출 분석**은 현재 매출을 발생시키는 유저군이 어떻게 구성되었는지, 그 추이 변화가 어떻게 되는지 분석합니다.







---



# 분석을 위한 기본 설정

## 기본 라이브러리 설정

In [ ]:
!pip install pandas folium

In [ ]:
import pandas as pd 
import numpy as np
import folium
import pickle

## Google Drive 마운트

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


## BigQuery 연동을 위한 기본 설정

In [ ]:
from google.colab import auth
from google.cloud import bigquery
from google.colab import data_table

project = 'crested-drive-372522' # Project ID inserted based on the query results selected to explore
location = 'US' # Location inserted based on the query results selected to explore
client = bigquery.Client(project=project, location=location)
data_table.enable_dataframe_formatter()
auth.authenticate_user()




---



# 로컬팜의 현재 상황 및 주요 이슈 

> **분석 진행에 앞서 수강생 분들께 전달되는 가상의 업체 상황**
- 21년 7월 목동의 유승상가에 픽업존 운영을 시작으로 현재는 총 8개의 매장을 운영중
- 22년 11월 서울지역 과일전문 다판다마켓을 인수(10월 말 부터 시범판매 시작, 11월 둘째주에 매장 오픈) 
- 물품을 소싱하는 판매자는 최초 (김지은-4f1d3d66, 양민석-34e92532, 손미경-afe78ffc) 3명으로 시작하였으나, 다판다마켓 인수와 함께 10월 부터 (김정식-2cca8b6e)님 합류.
- 현재 내부 인력의 대부분은 상품 소싱 및 배송에 투입되어 매장별 사용자 특징이나 앱 서비스 개선점에 대해서는 정확히 파악하기 어려운 상황.
- 최근에는 매출을 올리기 위해 매장을 늘리는게 좋을지, 기존 매장관리에 주력하는게 좋을지 고민하고 있으나 뚜렷한 답을 찾지 못한 상황.



---



# **[결론 및 제언]**

- 리포트의 서두에는 분석을 통해 확인된 지표 현황 또는 인사이트에 대해 요약한 내용을 작성합니다.
- 순서상 결론 부분은 리포트의 말미에 작성되는게 맞으나 두괄식 형태로 결론에 대해 먼저 전달하고 상세 내용을 나열하는 형태로 문서를 작성하면 리포트 열람자의 시간을 아껴줄 수 있습니다.
- 만약 분석을 통해 도출된 가설이나, 제안하고 싶은 내용이 있다면 해당 내용을 포함해서 작성합니다. (중요 ✨)


---



# **[ 오프라인 매장 현황 ]**

## < 매장 정보 >

In [ ]:
#@title Make DataFrame

## << shopsInfosDf: 매장 정보 테이블 생성 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# shopsInfosDf = query_job.to_dataframe()

## << 매장 정보 테이블 - 위치, 오픈일 >>

with open("/content/drive/MyDrive/sql_analysis_for_beginners_pickle/shopsInfosDf", "rb" ) as file:
    shopsInfosDf = pickle.load(file)

In [ ]:
#@title Show Table
shopsInfosDf.replace(np.NaN, 0, inplace=True)
shopsInfosDf.style.format({
    "sales_05m": "{:,.0f}",
    "sales_06m": "{:,.0f}",
    "sales_07m": "{:,.0f}",
    "sales_08m": "{:,.0f}",
    "sales_09m": "{:,.0f}",
    "sales_10m": "{:,.0f}",
    "sales_11m": "{:,.0f}",}).bar(['sales_05m', 'sales_06m', 'sales_07m', 'sales_08m', 'sales_09m', 'sales_10m', 'sales_11m'], color='#d65f5f',).hide_index()

> **Note**

- 11월에 오픈한 (GS영등포당산점, 다이소 난곡사거리점)은 기존 다판다마켓의 판매지역이며, (더현대서울) 지점은 서울시 창업지원을 받아 입점 

> **Comment**

- 전체 매장의 11월 매출은 전월比 160% 상승
- 유승상가 지점의 경우 5월 이후 지속적인 매출 하락세였으나 11월에 전월比 매출 78% 상승
- 6월에 신규 오픈한 4개 지점 또한 8월 이후 매출 하락세에 들어갔으나 11월에 전월比 매출 (23% ~ 136%) 상승
- 11월에 신규 입점한 2개(GS영등포당산점, 다이소 난곡사거리점) 지점의 경우 11월 전체 매출의 약 30% 차지

> **Tip**

- 표나 그래프를 공유할 경우 특이점이나, 추가적으로 살펴봐야 하는 내용들 위주로 코멘트를 달아주며
- 분석가는 해당 지점들을 토대로 분석 포인트들을 발굴해 냅니다. (데이터 해석 과정을 통한 EDA)

## < 오프라인 매장 및 결제유저 분포 >

In [ ]:
#@title Make DataFrame

## << novPickupUniquePu: 11월 기준 - 매장별 결제 유저별 거주지 및 누적 결제액  >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# novPickupUniquePu = query_job.to_dataframe()


## << storesRegionDf: 오프라인 매장 위치 정보 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# storesRegionDf = query_job.to_dataframe()


with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/novPickupUniquePu", "rb" ) as file:
    novPickupUniquePu = pickle.load(file)

with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/storesRegionDf", "rb" ) as file:
    storesRegionDf = pickle.load(file)

In [ ]:
#@title Visualization
from folium.plugins import MarkerCluster

## << 핀 포인트 - 초기 지도 위치 설정 >>
latitude = 37.5161 # 위도
longitude = 126.8967 # 경도

m = folium.Map(
    location=[latitude, longitude],
    zoom_start=13,
)

mrkerCluster = MarkerCluster().add_to(m)  

## << 매장 위치 표시 >>
for lat, long, name in zip(storesRegionDf['x'], 
                           storesRegionDf['y'], 
                           storesRegionDf['pickup_shop_name']):
    folium.Marker(location = [lat, long], popup=name, icon=folium.Icon(color='red', icon='star')).add_to(m)

## << 구매 유저 - 위치 표시 >>
for lat, long in zip(novPickupUniquePu['x'], 
                     novPickupUniquePu['y']):
    folium.Marker([lat, long], icon = folium.Icon(color="blue")).add_to(mrkerCluster)
    
m

> **Comment**
- 주거 밀집 지역에 위치한 매장일수록 결제 유저가 몰려있는 것을 확인할 수 있으며
- 유사한 입지 임에도, 매장별로 결제유저수에 차이가 나는 것으로 보아 매장별 퍼포먼스(구매력/재구매율/선호상품/거리 분포 등) 분석이 필요

> **Tip**
- 오프라인 기반 서비스의 경우 외부요인(코로나, 입지, 경쟁사 입점, 매장 임대료 등)에 의한 서비스 의존도가 크기 때문에 
- 객관적인 관점으로 데이터를 바라보기 위해서는 실제 매장 위치와 주변 입지에 대한 이해가 필요하며
- 필요시 현장답사를 하는 것도 데이터를 이해하는데 큰 도움이 됩니다.  

# **[ 사용자 유입 현황 분석 ]**

## < 요약 ✨ >

> **사용자 유입 현황 분석을 통해 전달하고 싶은 내용을 작성합니다 (1)**

- 관련된 상세 내용을 작성합니다.
- 관련된 상세 내용을 작성합니다.

> **사용자 유입 현황 분석을 통해 전달하고 싶은 내용을 작성합니다 (2)**

- 관련된 상세 내용을 작성합니다.
- 관련된 상세 내용을 작성합니다.

> **Tip**

- 분석 리포트에서 전달하고자 하는 내용이 길어질수록 상위 목차 서두에 요약본을 추가로 작성해 두면 열람자가 문서의 흐름을 놓치지 않는데 도움이 됩니다.

## < MAU, NRU >

In [ ]:
#@title Make DataFrame

## << mauDf: 월간 활성 유저수 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# mauDf = query_job.to_dataframe()


## << monthlyNruDf: 월간 가입 유저수 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# monthlyNruDf = query_job.to_dataframe()

with open("/content/drive/MyDrive/sql_analysis_for_beginners_pickle/mauDf", "rb" ) as file:
    mauDf = pickle.load(file)

with open("/content/drive/MyDrive/sql_analysis_for_beginners_pickle/monthlyNruDf", "rb" ) as file:
    monthlyNruDf = pickle.load(file)

In [ ]:
#@title Visualization

# * 🔥 가공된 DataFrame을 Plotly를 통해 시각화 합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.

%%html
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://plotly.com/~noru/1.embed" height="525" width="100%"></iframe>

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

## < 지역별 MAU, NRU >

In [ ]:
#@title Make DataFrame

## << mauByRegionDf: 월간 지역별 활성 유저수 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# mauByRegionDf = query_job.to_dataframe()


# ## << monthlyNruByRegionDf: 월간 지역별 가입 유저수 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# monthlyNruByRegionDf = query_job.to_dataframe()


## < monthlyAuAndNru: 월간 지역별 활성 유저수, 가입 유저수 >
#
# mauByRegionDf = monthlyNruByRegionDf.rename(columns={'login_year_month':'year_month'})
# mauByRegionDf['category'] = 'AU'
# monthlyNruByRegionDf = monthlyNruByRegionDf.rename(columns={'create_year_month':'year_month'})
# monthlyNruByRegionDf['category'] = 'NRU'
# monthlyAuAndNru = pd.concat([mauByRegionDf, monthlyNruByRegionDf], ignore_index=True) 

# # user_group 한글로 변경
# monthlyAuAndNru['user_group'] = np.where(monthlyAuAndNru['user_group'] == 'new', '신규지역', monthlyAuAndNru['user_group'])
# monthlyAuAndNru['user_group'] = np.where(monthlyAuAndNru['user_group'] == 'decrease', '감소지역', monthlyAuAndNru['user_group'])
# monthlyAuAndNru['user_group'] = np.where(monthlyAuAndNru['user_group'] == 'increase_0_10', '10%이하_증가지역', monthlyAuAndNru['user_group'])
# monthlyAuAndNru['user_group'] = np.where(monthlyAuAndNru['user_group'] == 'increase_10_20', '10%초과_20%이하_증가지역', monthlyAuAndNru['user_group'])
# monthlyAuAndNru['user_group'] = np.where(monthlyAuAndNru['user_group'] == 'increase_20_30', '20%초과_30%이하_증가지역', monthlyAuAndNru['user_group'])
# monthlyAuAndNru['user_group'] = np.where(monthlyAuAndNru['user_group'] == 'increase_30_more', '30%_초과_증가지역', monthlyAuAndNru['user_group'])


# ## << novShopAndPuRegion: 11월 매출 기준 매장별 구매자 거주지역별 매출 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# novShopAndPuRegion = query_job.to_dataframe()

with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/mauByRegionDf", "rb" ) as file:
    mauByRegionDf = pickle.load(file)

# with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/monthlyNruDf", "rb" ) as file:
#     monthlyNruDf = pickle.load(file)

with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/monthlyAuAndNru", "rb" ) as file:
    monthlyAuAndNru = pickle.load(file)

with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/novShopAndPuRegion", "rb" ) as file:
    novShopAndPuRegion = pickle.load(file)

In [ ]:
#@title 매장별 거주지역별 11월 매출

## << 매장별 구매자 거주 지역별 11월 매출 테이블 >>
novShopAndPuRegion.fillna(0)

order_year_month pickup_shop_name  Sillim_dong  Jowon_dong  Guro2_dong  \
0          2022-11        픽업존(유승상가)            0           0           0   
1          2022-11       픽업존(메이비카페)            0     3092100     2149800   
2          2022-11  픽업존(서울드림신용협동조합)            0           0           0   
3          2022-11  픽업존(GS25 목동3동점)            0           0           0   
4          2022-11   픽업존(참맛부대찌개아구찜)            0           0           0   
5          2022-11    픽업존(GS영등포당산점)            0           0           0   
6          2022-11  픽업존(다이소 난곡사거리점)     10452400           0           0   
7          2022-11       픽업존(더현대서울)            0           0           0   

   Sindorim_dong  Doksan3_dong  Mok_dong  Dangsandong4_ga  Dangsandong5_ga  \
0              0             0  51315800                0                0   
1              0        837700   9565500                0                0   
2        9418500             0         0                0                0   
3         179400             0   8660200                0                0   
4              0             0         0                0                0   
5              0         72000    813400         10493300         21598900   
6              0       1477100         0                0                0   
7              0             0         0                0                0   

   Daerim2_dong  Mullaedong3_ga  Yangpyeongdong3_ga  Yangpyeongdong4_ga  \
0             0         2748000                   0                   0   
1      11978700          325300                   0                   0   
2             0           76100                   0                   0   
3             0               0                   0                   0   
4             0         6137600                   0                   0   
5             0               0             2232800             1193600   
6         88600               0                   0                   0   
7             0               0                   0                   0   

   Yeouido_dong  
0             0  
1             0  
2             0  
3             0  
4             0  
5        173700  
6         84900  
7       1199500

> **Comment**

- 표를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

In [ ]:
#@title Visualization-1

## << 지역별 AU - Bar Chart >>

# * 🔥 가공된 DataFrame을 Plotly를 통해 시각화 합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.

%%html
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://plotly.com/~noru/7.embed" height="525" width="100%"></iframe>

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

In [ ]:
#@title Visualization-2

## << 지역별 AU, NRU >>

# * 🔥 가공된 DataFrame을 Plotly를 통해 시각화 합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.

%%html
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://plotly.com/~noru/9.embed" height="525" width="100%"></iframe>

> **Note**

- user_group 분류기준: 11월 지표의 전월比 증감률을 기준으로 계산

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

> **Tip**

- 앞서 전달한 Bar chart에서 그룹간 상대비교가 어려운 경우, *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*

## < 가입 연도별/월별 MAU >



In [ ]:
#@title Make DataFrame

## << yearlyAuDf: 가입 연도별 활성 유저수 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# yearlyAuDf = query_job.to_dataframe()

## << monthlyAuDf: 가입 연월별 활성 유저수 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# monthlyAuDf = query_job.to_dataframe()

## << auChurnedRateDf: 가입 연월별 - 최초 유입시점 볼륨 대비 미접속률 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# auChurnedRateDf = query_job.to_dataframe()
# auChurnedRateDf['time_order'] = 'M+' + auChurnedRateDf['time_order'].astype(str)
# auChurnedRateDf = auChurnedRateDf.rename(columns={"first_user_cnt":"M+0_user_count"})

## << auChurnedCntAndRateDf: 가입 연월별 - 월간(접속 유저수, 재접속률) - M+0부터 추적 가능한 2022-05 유입 유저부터 잘라냄 >>
# auChurnedCntAndRateDf = auChurnedRateDf[auChurnedRateDf['create_year_month'] >= '2022-05']\
# .sort_values(by=["create_year_month", "login_year_month"])\
# .melt(id_vars=["create_year_month", "login_year_month", "create_year", "time_order"], value_vars=["user_cnt", "rate_of_change"]) 


## << auChurnedRateByRegionDf: 가입 연월별 지역별 - 최초 유입시점 볼륨 대비 미접속률 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# auChurnedRateByRegionDf = query_job.to_dataframe()
# auChurnedRateByRegionDf['time_order'] = 'M+' + auChurnedRateByRegionDf['time_order'].astype(str)
# auChurnedRateByRegionDf = auChurnedRateByRegionDf.rename(columns={"first_user_cnt":"M+0_user_count"})

## << auChurnedCntAndRateDf: 가입 연월별 지역별 - 월간(접속 유저수, 재접속률) - M+0부터 추적 가능한 2022-05 유입 유저부터 잘라냄 >>
# auChurnedCntAndRateByRegionDf = auChurnedRateByRegionDf[auChurnedRateByRegionDf['create_year_month'] >= '2022-05']\
# .sort_values(by=["create_year_month", "login_year_month", "region"])\
# .melt(id_vars=["create_year_month", "login_year_month", "create_year", "region", "time_order"], value_vars=["user_cnt", "rate_of_change"]) 


# with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/yearlyAuDf", "wb" ) as file:
#     pickle.dump(yearlyAuDf, file)

# with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/monthlyAuDf", "wb" ) as file:
#     pickle.dump(monthlyAuDf, file)

# with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/auChurnedRateDf", "wb" ) as file:
#     pickle.dump(auChurnedRateDf, file)

# with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/auChurnedCntAndRateDf", "wb" ) as file:
#     pickle.dump(auChurnedCntAndRateDf, file)

# with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/auChurnedRateByRegionDf", "wb" ) as file:
#     pickle.dump(auChurnedRateByRegionDf, file)

# with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/auChurnedCntAndRateByRegionDf", "wb" ) as file:
#     pickle.dump(auChurnedCntAndRateByRegionDf, file)



with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/yearlyAuDf", "rb" ) as file:
    yearlyAuDf = pickle.load(file)

with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/monthlyAuDf", "rb" ) as file:
    monthlyAuDf = pickle.load(file)

with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/auChurnedRateDf", "rb" ) as file:
    auChurnedRateDf = pickle.load(file)

with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/auChurnedCntAndRateDf", "rb" ) as file:
    auChurnedCntAndRateDf = pickle.load(file)

with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/auChurnedRateByRegionDf", "rb" ) as file:
    auChurnedRateByRegionDf = pickle.load(file)

with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/auChurnedCntAndRateByRegionDf", "rb" ) as file:
    auChurnedCntAndRateByRegionDf = pickle.load(file)


In [ ]:
#@title Visualization-1

## << 가입 연도별 월간 활성 유저수 - Bar Chart >>

# * 🔥 가공된 DataFrame을 Plotly를 통해 시각화 합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.

%%html
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://plotly.com/~noru/11.embed" height="525" width="100%"></iframe>

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

> **Tip**

- 지표를 (가입시점/지역/결제유무/커스텀그룹) 등으로 나누어 보고자 할 경우, *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*
- , *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*


In [ ]:
#@title Visualization-2

## << 가입 연월별 월간 활성 유저수 - Bar Chart >>

# * 🔥 가공된 DataFrame을 Plotly를 통해 시각화 합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.

%%html
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://plotly.com/~noru/15.embed" height="525" width="100%"></iframe>

> **Comment**

- 표를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

In [ ]:
#@title Visualization-3

## << 가입연월별 최초유입시점대비 재접속률 변화 >>

# * 🔥 가공된 DataFrame을 Plotly를 통해 시각화 합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.

%%html
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://plotly.com/~noru/17.embed" height="350" width="100%"></iframe>

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

> **Tip**

- 위와 같이 특정 시점의 수치를 100%로 두고 시간의 흐름에 따라, *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*
- , *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*
- , *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*


## < 가입 월별 지역별 M+1 재접속률 >

In [ ]:
#@title Visualization-1

## << 가입연월별 최초유입시점 대비 M+1 재접속률 변화 >>

# * 🔥 가공된 DataFrame을 Plotly를 통해 시각화 합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.

%%html
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://plotly.com/~noru/19.embed" height="525" width="100%"></iframe>

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

> **Tip**

- 한 화면에서 표현되는 정보의 양이 많을수록, *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*
- 현황 분석시 특정 이슈의 원인을 끝까지 파고드는것 보다는, *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*

# **[ 잔존율 분석 ]**

## < 요약 ✨ >

> **사용자 유입 현황 분석을 통해 전달하고 싶은 내용을 작성합니다 (1)**

- 관련된 상세 내용을 작성합니다.
- 관련된 상세 내용을 작성합니다.

> **사용자 유입 현황 분석을 통해 전달하고 싶은 내용을 작성합니다 (2)**

- 관련된 상세 내용을 작성합니다.
- 관련된 상세 내용을 작성합니다.

> **Tip**

- 분석 리포트에서 전달하고자 하는 내용이 길어질수록 상위 목차 서두에 요약본을 추가로 작성해 두면 열람자가 문서의 흐름을 놓치지 않는데 도움이 됩니다.

## < 신규 유저 잔존율 현황 >

In [ ]:
#@title Make DataFrame

## << monthlyRetByUserType: 유저 타입별 월간 일평균 D+day 잔존율 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# monthlyRetByUserType = query_job.to_dataframe()


## << dauNdayRet: 유저 타입별 일간 D+day 잔존율 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# dauNdayRet = query_job.to_dataframe()


with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/monthlyRetByUserType", "rb" ) as file:
    monthlyRetByUserType = pickle.load(file)

with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/dauNdayRet", "rb" ) as file:
    dauNdayRet = pickle.load(file)

In [ ]:
#@title Visualization-1 

## << 신규 유저 월간 일평균 N-day 잔존율 >>

%%html
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://plotly.com/~noru/21.embed" height="525" width="100%"></iframe>

> **Note**

- 지표 해석시 참고가 필요한 내용을 작성합니다.

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

In [ ]:
#@title Visualization-2

## << 신규 유저 월간 일평균 N-day 잔존율 >>

# * 🔥 가공된 DataFrame을 Plotly를 통해 시각화 합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.

%%html
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://plotly.com/~noru/23.embed" height="525" width="100%"></iframe>

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

> **Tip**

- 월간 지표를 보았다면, *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*
- 특히 평균을 계산하는 경우, *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*

## < 재방문 유저 잔존율 현황 >

In [ ]:
#@title Make DataFrame

## << monthlyRetByUserType2: 유저 타입별 월간 일평균 D+day 잔존율 - 재방문 유저에 대한 분류기준이 다르다. 신규유저는 가입월 동안은 계속 신규유저로 분류되는 방식. 즉 재방문 유저 기준으로 월간 평균 잔존율 계산시 모수에서 당월에 유입된 신규유저가 제외된다. >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# monthlyRetByUserType2 = query_job.to_dataframe()



## << dauNdayRet2: 유저 타입별 일간 D+day 잔존율 - 재방문 유저에 대한 분류기준이 다르다. 신규유저는 가입월 동안은 계속 신규유저로 분류되는 방식. 즉 재방문 유저 기준으로 월간 평균 잔존율 계산시 모수에서 당월에 유입된 신규유저가 제외된다. >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# dauNdayRet2 = query_job.to_dataframe()


with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/monthlyRetByUserType2", "rb" ) as file:
    monthlyRetByUserType2 = pickle.load(file)

with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/dauNdayRet2", "rb" ) as file:
    dauNdayRet2 = pickle.load(file)

In [ ]:
#@title Visualization-1 

## << 재방문유저 월간 일평균 N-day 잔존율 >>

# * 🔥 가공된 DataFrame을 Plotly를 통해 시각화 합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.

%%html
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://plotly.com/~noru/25.embed" height="525" width="100%"></iframe>

> **Note**

- 지표 해석시 참고가 필요한 내용을 작성합니다.


> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.


> **Tip**

- 일간 단위에서 신규 또는 재방문 유저를 분류하는 기준은 당일 가입 여부로 판단되므로, *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*
  - 1안) ***
  - 2안) ***
  - 3안) ***

In [ ]:
#@title Visualization-2

## << 재방문 유저 N-day 잔존율 >>

# * 🔥 가공된 DataFrame을 Plotly를 통해 시각화 합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.

%%html
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://plotly.com/~noru/27.embed" height="525" width="100%"></iframe>


> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

> **Tip**

- 분석시 꼭 확인해줘야 하는 기본 지표이지만 특이사항이 없는 경우라면, *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*

## < 지역별 잔존율 현황 >

In [ ]:
#@title Make DataFrame

## << weeklyRetByRegion: 지역별 주간 일평균 D+day 잔존율 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# weeklyRetByRegion = query_job.to_dataframe()

with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/weeklyRetByRegion", "rb" ) as file:
    weeklyRetByRegion = pickle.load(file)

In [ ]:
#@title Visualization-1

# * 🔥 가공된 DataFrame을 Plotly를 통해 시각화 합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.

%%html
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://plotly.com/~noru/29.embed" height="400" width="100%"></iframe>

In [ ]:
#@title Visualization-2

# * 🔥 가공된 DataFrame을 Plotly를 통해 시각화 합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.

%%html
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://plotly.com/~noru/31.embed" height="550" width="100%"></iframe>

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.


# **[ 매출 현황 분석 ]**

## < 요약 ✨ >

> **사용자 유입 현황 분석을 통해 전달하고 싶은 내용을 작성합니다 (1)**

- 관련된 상세 내용을 작성합니다.
- 관련된 상세 내용을 작성합니다.

> **사용자 유입 현황 분석을 통해 전달하고 싶은 내용을 작성합니다 (2)**

- 관련된 상세 내용을 작성합니다.
- 관련된 상세 내용을 작성합니다.

> **Tip**

- 분석 리포트에서 전달하고자 하는 내용이 길어질수록 상위 목차 서두에 요약본을 추가로 작성해 두면 열람자가 문서의 흐름을 놓치지 않는데 도움이 됩니다.

## < 월간 매출지표 현황 >

In [ ]:
#@title Make DataFrame

## << monthlySalesIndexDf: 월간 매출 기본지표 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# monthlySalesIndexDf = query_job.to_dataframe()


## << weeklySalesIndexDf: 주간 매출 기본지표 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# weeklySalesIndexDf = query_job.to_dataframe()


with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/monthlySalesIndexDf", "rb" ) as file:
    monthlySalesIndexDf = pickle.load(file)

with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/weeklySalesIndexDf", "rb" ) as file:
    weeklySalesIndexDf = pickle.load(file)

In [ ]:
#@title Visualization - 1

## << 월간 지역별 신규 유저수  >>

import plotly.graph_objects as go
from plotly.subplots import make_subplots


fig = make_subplots(
    rows=6, cols=1, 
    vertical_spacing=0.04,
    specs=[[{"secondary_y": True}], [{"secondary_y": True}], [{"secondary_y": True}], [{"secondary_y": True}], [{"secondary_y": True}], [{"secondary_y": True}]], 
)

fig.add_trace(
    go.Bar(    
        x=monthlySalesIndexDf['year_month'], 
        y=monthlySalesIndexDf['MAU'],
        name='MAU',
        marker_color="skyblue", # MAU 11월 색 강조        
    ),
    secondary_y=False,
    row=1, col=1,
)

fig.add_trace(
    go.Scatter(
        x=monthlySalesIndexDf['year_month'], 
        y=monthlySalesIndexDf['PUR'], 
        name='PUR', 
        mode='lines+markers+text', 
        text=monthlySalesIndexDf['PUR'], 
        textposition='top center',
        texttemplate='%{text:.1%}',
        hovertemplate="%{y:.1%}",
    ),
    secondary_y=True,
    row=1, col=1,
)

fig.add_trace(
    go.Scatter(
        x=monthlySalesIndexDf['year_month'], 
        y=monthlySalesIndexDf['SALES'], 
        mode='lines+markers+text', 
        name='SALES', 
        text=monthlySalesIndexDf['SALES'],
        textposition='top center',
        texttemplate='%{text:,}원',
        hovertemplate="%{y:,}원",
    ),
    row=2, col=1
)

fig.add_trace(
    go.Scatter(
        x=monthlySalesIndexDf['year_month'], 
        y=monthlySalesIndexDf['PU'], 
        mode='lines+markers+text', 
        name='PU',
        text=monthlySalesIndexDf['PU'],
        textposition='top center',
        texttemplate='%{text:,}명',
        hovertemplate="%{y:,}명",
    ),
    row=3, col=1
)

fig.add_trace(
    go.Scatter(
        x=monthlySalesIndexDf['year_month'], 
        y=monthlySalesIndexDf['ARPPU'], 
        mode='lines+markers+text', 
        name='ARPPU',
        text=monthlySalesIndexDf['ARPPU'],
        textposition='top center',
        texttemplate='%{text:,}원',
        hovertemplate="%{y:,}원",
    ),
    row=4, col=1
)


fig.add_trace(
    go.Scatter(
        x=monthlySalesIndexDf['year_month'], 
        y=monthlySalesIndexDf['PURCHASE_CNT'], 
        mode='lines+markers+text', 
        name='PURCHASE_CNT',
        text=monthlySalesIndexDf['PURCHASE_CNT'],
        textposition='top center',
        texttemplate='%{text:,}개',
        hovertemplate="%{y:,}개",
    ),
    row=5, col=1
)

fig.add_trace(
    go.Scatter(
        x=monthlySalesIndexDf['year_month'], 
        y=monthlySalesIndexDf['REGISTRATION_CNT'], 
        mode='lines+markers+text', 
        name='REGISTRATION_CNT',
        text=monthlySalesIndexDf['REGISTRATION_CNT'],
        textposition='top center',
        texttemplate="%{text:,}개",
        hovertemplate="%{y:,}개",
    ),
    row=6, col=1
)

fig.update_layout(
    
    {
        "title": {
            "text": "<b>< 매출지표(SALES, PU, PUR, ARPPU) 월간 추이 ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
        "yaxis2": { 
            "title": "PUR",
            "tickformat": '.0%',
            "range": [0.25, 0.6],
        },
        "yaxis1": {
            "range":[0, 8000],
            "tickformat": ',',
            "title": "MAU(명)"
        },
        "yaxis3": {
            "range":[0, 200000000],
            "title": "SALES(원)"
        },
        "yaxis5": {
            "range":[0, 3000],
            "title": "PU(명)",
            "tickformat": ","
        },
        "yaxis7": {
            "range":[20000, 80000],
            "title": "ARPPU(원)"
        },
        "yaxis9": {
            "range":[0, 15000],
            "title": "구매횟수(개)"
        },
        "yaxis11": {
            "range":[0, 400],
            "title": "상품등록수(개)"
        },     
        "template":'plotly',
        "legend_traceorder": "normal", #normal(default - 데이터 순서대로), reversed
        "height": 1200
    },    
)

fig.update_layout(hovermode="x")
fig['layout']['yaxis1']['showgrid'] = False
fig.update_xaxes(showgrid=False)
fig.update_xaxes(title = "", tick0 = "2022-05", dtick="M1", tickformat="%Y-%m")
fig.update_layout(height = 900)

fig.show()

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.


> **Tip**

- 매출 지표의 경우 SALES와 함께, *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*
- , *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*
- , *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*

## < 매장별 구매 형태 비교 >

In [ ]:
!pip install haversine

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
#@title Make DataFrame

## << novSalesInfoByShopDf: 11월 매장별 유저별 구매횟수, 구매액 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# novSalesInfoByShopDf = query_job.to_dataframe()

# << distBetweenLocalAndShopDf : 11월 구매유저 - 주거지 <-> 매장 거리 분포 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# distBetweenLocalAndShopDf = query_job.to_dataframe()


## << 데이터 변환: 11월 픽업상품 구매 유저의 (매장 <-> 설정지역)간의 거리 계산 >>

##  latitude(위도) = x, longitude(경도) = y

# from haversine import haversine

#--------------------------------------------------------------
# (haversine() 연산을 위해 픽업장소와, 본인지역에 대한 위도와 경도를 묶음 형태로 변환
#--------------------------------------------------------------

## 이렇게 스트링으로 넣어주면 안되고
# novPickupUniquePu['pickup_location'] = novPickupUniquePu[['pickup_lat', 'pickup_long']].apply(lambda row: '(' + ', '.join(row.values.astype(str)) + ')', axis=1)
# novPickupUniquePu['preferred_location'] = novPickupUniquePu[['preferred_lat', 'preferred_long']].apply(lambda row: '(' + ', '.join(row.values.astype(str)) + ')', axis=1)

## 이렇게 튜플 형태로 좌표를 묶어서 넣어줘야, 밑에서 havershine() 함수가 작동 🔥
# distBetweenLocalAndShopDf['pickup_location'] = distBetweenLocalAndShopDf[['shop_x', 'shop_y']].apply(lambda x: (x['shop_x'], x['shop_y']), axis=1)
# distBetweenLocalAndShopDf['home_location'] = distBetweenLocalAndShopDf[['home_x', 'home_y']].apply(lambda x: (x['home_x'], x['home_y']), axis=1)


#--------------------------------------------------------------
# (본인이 설정한 동네 위치와, 픽업 장소 위치간의 km 계신)
#--------------------------------------------------------------

# def calculateDistance(x):
#     return haversine(x[0], x[1], unit = 'km')
    
# distBetweenLocalAndShopDf['distance'] = distBetweenLocalAndShopDf[['home_location', 'pickup_location']].apply(calculateDistance, axis=1) 


with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/novSalesInfoByShopDf", "rb" ) as file:
    novSalesInfoByShopDf = pickle.load(file)

with open( "/content/drive/MyDrive/sql_analysis_for_beginners_pickle/distBetweenLocalAndShopDf", "rb" ) as file:
    distBetweenLocalAndShopDf = pickle.load(file)

In [ ]:
#@title Visualization - 1

import plotly.express as px

fig = px.histogram(novSalesInfoByShopDf, x="sales", color="pickup_shop_name", 
                   marginal="box", # can be rug, box, violin
                   histnorm='percent', #percent, probability, density
                   barmode='overlay', # stack, group, overlay
                   hover_data=novSalesInfoByShopDf.columns)

fig.update_layout(
    {
        "title": {
            "text": "<b>< 11월 매장별 누적 구매액 분포 ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
    },
)

fig.update_xaxes(title="월간 누적 구매액", row=1)

fig.show()


> **Note**

- 지표 해석시 참고가 필요한 내용을 작성합니다.

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.


> **Tip**

- 그룹별 분포를 비교할 때, *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*
- 비교 집단간 스케일 차이가 크다면, *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*

In [ ]:
#@title Visualization - 2

import plotly.express as px

fig = px.histogram(novSalesInfoByShopDf, x="purchase_cnt", color="pickup_shop_name", marginal="box", # can be rug, box, violin
                   histnorm='percent', #percent, probability, density
                   barmode='overlay', # stack, group, overlay
                   hover_data=novSalesInfoByShopDf.columns)

fig.update_layout(
    {
        "title": {
            "text": "<b>< 11월 매장별 누적 구매횟수 분포 ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
    },
)

fig.update_xaxes(title="월간 누적 구매 횟수", row=1)
fig.show()

> **Note**

- 지표 해석시 참고가 필요한 내용을 작성합니다.

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

In [ ]:
#@title Visualization - 3

import plotly.express as px

fig = px.histogram(distBetweenLocalAndShopDf, x="distance", color="pickup_shop_name", marginal="box", # can be rug, box, violin
                   histnorm='percent', #percent, probability, density
                   barmode='overlay', # stack, group, overlay
                   hover_data=distBetweenLocalAndShopDf.columns)

fig.update_layout(
    {
        "title": {
            "text": "<b>< 11월 매장별 누적 구매횟수 분포 ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
        "height": 500,
    },
)

fig.update_xaxes(title="거주지 ↔ 매장 거리(km)", row=1)
fig.show()

> **Note**

- 지표 해석시 참고가 필요한 내용을 작성합니다.

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

In [ ]:
#@title Visualization - 4

import plotly.express as px

fig = px.histogram(distBetweenLocalAndShopDf, x="distance", color="pickup_shop_name", marginal="box", # can be rug, box, violin
                   histnorm='percent', #percent, probability, density
                   barmode='overlay', # stack, group, overlay
                   facet_col = "user_group",
                   category_orders={"user_group": ["g_1만원", "g_1만원_2만원", "g_2만원_3만원", "g_3만원_4만원", 'g_4만원_more']},
                   hover_data=distBetweenLocalAndShopDf.columns)

fig.update_layout(
    {
        "title": {
            "text": "<b>< 11월 매장별 누적 구매횟수 분포 ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
    },
)

fig.update_xaxes(title="거주지 ↔ 매장 거리(km)", row=1)
fig.show()

> **Note**

- 지표 해석시 참고가 필요한 내용을 작성합니다.

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.


## < 상품 판매 순위 >

In [ ]:
#@title Make DataFrame

## << novSalesInfoByUserDf: 유저별 11월 누적 결제액 기준, 매장별 상품별 누적 구매액 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# novSalesInfoByUserDf = query_job.to_dataframe()

# 매장 <-> 집 거리정보 붙이기
# novSalesInfoByUserDf = pd.merge(novSalesInfoByUserDf, distBetweenLocalAndShopDf[['user_id', 'pickup_shop_name', 'distance']], on = ['user_id', 'pickup_shop_name'], how = 'left')


with open("/content/drive/MyDrive/sql_analysis_for_beginners_pickle/novSalesInfoByUserDf", "rb" ) as file:
    novSalesInfoByUserDf = pickle.load(file)

In [ ]:
#@title Visualization - 1

fig = px.scatter(novSalesInfoByUserDf.rename(columns={'pickup_shop_name':'매장'}),
                 x = 'distance',
                 y = 'total_sales',
                 color = 'product_title',
                 facet_col = 'user_group', #, facet_col_wrap=4) # trendline='ols'
                 facet_row = '매장',
                 category_orders={"user_group": ["g_1만원", "g_1만원_2만원", "g_2만원_3만원", "g_3만원_4만원", 'g_4만원_more'],
                                  "매장": ["픽업존(유승상가)", "픽업존(메이비카페)", "픽업존(서울드림신용협동조합)", "픽업존(GS25 목동3동점)", "픽업존(참맛부대찌개아구찜)", "픽업존(GS영등포당산점)", "픽업존(다이소 난곡사거리점)", "픽업존(다이소 난곡사거리점)", "픽업존(더현대서울)"]},
                 )

fig.update_layout(
  {
    "title": {
        "text": "<b>< 11월 누적구매액별 매장별 상품 판매액 ><b>",
        "x": 0.5,
        "y": 0.99,
        "font": {
            "size": 13
        }
    },
    "height": 1600, 
  },
)
fig.show()

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.
  - 위의 그래프를 통해 어떤 메세지를 전달할 수 있을까요?
  - 이런 시각화 과정을 통해 어떤 정보를 전달하고 싶었던 걸까요?

> **Tip**

- 한눈에 알아보기 어려운 데이터 일수록, *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*
- *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*

In [ ]:
#@title Make DataFrame

## << novSalesRankDf: 11월 매장별 상품별 판매 순위 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# novSalesRankDf = query_job.to_dataframe()


with open("/content/drive/MyDrive/sql_analysis_for_beginners_pickle/novSalesRankDf", "rb" ) as file:
    novSalesRankDf = pickle.load(file)

In [ ]:
#@title Visualization - 2

# * 🔥 가공된 DataFrame을 Plotly를 통해 시각화 합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.

%%html
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://plotly.com/~noru/39.embed" height="450" width="100%"></iframe> 


> **Note**

- 지표 해석시 참고가 필요한 내용을 작성합니다.

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

In [ ]:
#@title Visualization - 3

# * 🔥 가공된 DataFrame을 Plotly를 통해 시각화 합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.

%%html
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://plotly.com/~noru/41.embed" height="450" width="100%"></iframe>

> **Note**

- 지표 해석시 참고가 필요한 내용을 작성합니다.

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

In [ ]:
#@title Visualization - 4

# * 🔥 가공된 DataFrame을 Plotly를 통해 시각화 합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.

%%html
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://plotly.com/~noru/43.embed" height="450" width="100%"></iframe>

> **Note**

- 지표 해석시 참고가 필요한 내용을 작성합니다.

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

## < 판매자별 매출 기여도 >

In [ ]:
#@title Make DataFrame

## << novSalesInfoByUserDf: 월별 판매자별 매출 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# monthlySalesBySellerDf = query_job.to_dataframe()



## << monthlySalesByShopAndSellerDf: 월별 매장별 판매자별 매출 >>
# query_job = client.query("""
#   select a.order_year_month, a.pickup_shop_name, c.nickname, sum(a.payment_amount) as sales
#   from `my_temp.daily_orders` as a
#   left join `localparm_dw.products` as b
#   on a.product_id = b.product_id
#   left join `my_temp.all_myinfos` as c
#   on b.user_id = c.user_id
#   where a.payment_status = 'completed'
#   group by a.order_year_month, a.pickup_shop_name, c.nickname
#   order by a.order_year_month, a.pickup_shop_name, c.nickname
# """)
# monthlySalesByShopAndSellerDf = query_job.to_dataframe()


with open("/content/drive/MyDrive/sql_analysis_for_beginners_pickle/monthlySalesBySellerDf", "rb" ) as file:
    monthlySalesBySellerDf = pickle.load(file)

with open("/content/drive/MyDrive/sql_analysis_for_beginners_pickle/monthlySalesByShopAndSellerDf", "rb" ) as file:
    monthlySalesByShopAndSellerDf = pickle.load(file)


In [ ]:
#@title Visualization - 1

## << 월간 판매자별 SALES >> 

import plotly.express as px

fig = px.bar(monthlySalesBySellerDf, 
              x="order_year_month", 
              y="sales", 
              color="nickname", 
              text="sales",
              # facet_row="region_name",
             )

fig.update_traces(texttemplate='%{text:,}원', textposition='inside',)

fig.update_layout(
    {
        "title": {
            "text": "<b>< 판매자별 월간 SALES ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
        "yaxis": { "title": "SALES(원)", "tickformat": ','  }, 
        "xaxis": {
            "title": "",
            "tick0": "2022-05",
            "dtick": 'M1',
            "tickformat": "%Y-%m"
        },
        "legend_title_text": "판매자 닉네임",
        "template":'plotly_white',
    }
)


fig.show()

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

In [ ]:
#@title Visualization - 2

## 월별 매장별 판매자별 매출 

import plotly.express as px

monthlySalesByShopAndSellerDf

fig = px.bar(monthlySalesByShopAndSellerDf, 
             x='order_year_month', 
             y='sales',
             text='sales',
             color='nickname',
             barmode="group", 
             facet_col="pickup_shop_name",
             facet_col_wrap=4,
             facet_row_spacing = 0.1, #  (float between 0 and 1) – Spacing between facet rows, in paper units. Default is 0.03 or 0.0.7 when facet_col_wrap is used.
             category_orders={"pickup_shop_name": ['픽업존(유승상가)', '픽업존(메이비카페)', '픽업존(서울드림신용협동조합)', '픽업존(GS25 목동3동점)', '픽업존(참맛부대찌개아구찜)', '픽업존(GS영등포당산점)', '픽업존(다이소 난곡사거리점)', '픽업존(더현대서울)'],
                              "order_year_month": ["2022-05", "2022-06", "2022-07", "2022-08", "2022-09", "2022-10", "2022-11"]},               
            )

fig.update_layout(
    {
        "title": {
            "text": "<b>< 월별 매장별 판매자별 매출 비교 ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
        "template":'plotly_white',
        "legend_traceorder": "reversed",
        "legend_title_text": "판매자 닉네임"
        
    }
)

fig.update_layout(height = 600)
fig.update_xaxes(showticklabels=True , matches=None)
fig.update_xaxes(title= "", tick0="2022-05", dtick="M1", tickformat="%Y-%m")
fig.update_yaxes(showticklabels=True)

fig.update_traces(textposition='inside', texttemplate='%{text:,}원',)

fig.show()


> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

## < 매출 기여도 구성 현황 >

In [ ]:
#@title Make DataFrame

## << monthlySalesGrowthAccountDf: 월간 매출 성장 회계 데이터 >>
#
# query_job = client.query("""
#
# * 🔥 SQL을 통해 BigQuery 테이블을 원하는 형태로 가공후 DataFrame으로 저장합니다.
# * 🔥 실제 코드는 수강시 확인할 수 있습니다.
#
# """)
# monthlySalesGrowthAccountDf = query_job.to_dataframe()


with open("/content/drive/MyDrive/sql_analysis_for_beginners_pickle/monthlySalesGrowthAccountDf", "rb" ) as file:
    monthlySalesGrowthAccountDf = pickle.load(file)

In [ ]:
#@title - Visualization - 1

## << 장표: SALES Growth Accounting  >> 

import plotly.express as px

fig = px.bar(monthlySalesGrowthAccountDf[['year_month', 'user_group', 'payment_amount']], 
             x=monthlySalesGrowthAccountDf['year_month'], 
             y=monthlySalesGrowthAccountDf['payment_amount'],
             text=monthlySalesGrowthAccountDf['payment_amount'],
             color=monthlySalesGrowthAccountDf['user_group'])

fig.update_layout(
    {
        "title": {
            "text": "<b>< SALES - Growth Accounting ><b>",
            "x": 0.5,
            "y": 0.9,
            "font": {
                "size": 13
            }
        },
        "yaxis": {
            "title": "SALES"    
        },
        "xaxis": {
            "title": "",
            "tick0": "2022-02",
            "dtick": 'M1',
            "tickformat": "%Y-%m"
        },
        "template":'plotly_white',
        "legend_traceorder": "reversed",
        "legend_title_text": "사용자 그룹"
    }
)

fig.update_traces(textposition='inside', texttemplate='%{text:,}원',)

fig.show()

> **Note**

- 사용자 그룹 정의
  - new_user : ***
  - retained_user : ***
  - resurrected_user : ***
  - churned_user : ***

> **Comment**

- 그래프를 통해 전달하고자 하는 메세지(정보/인사이트)를 작성합니다.

> **Tip**

- 유저의 형태를 잘 정의하여, *... 생략 (강의 수강을 통해 함께 공부 해봐요! 😉)*

---

# **[프로젝트 마무리]**

> **축하드립니다!** 🎉🎉🎉 

- 여기까지 무사히 따라오셨다면 여러분은 실무에서 다루는 (초급 ~ 일부는 중급) 수준의 SQL을 모두 경험해 보셨다고 말씀드리고 싶습니다. 
- 데이터분석은 정해진 틀도, 규칙도 없는 창조적 작업의 영역이라 생각합니다. 본 프로젝트에서 다룬 리포트 양식 또한 수신 대상이 누구인지, 분석 목적이 무엇인지에 따라 얼마든지 바뀔 수 있고 경우에 따라서는 정답이 아닐수 있습니다.
- 따라서 여기서 다룬 시각화 방법과 리포팅 가이드 라인들은 참고용으로만 활용하시되, 본인이 생각하는 더 나은 순서와 인사이트 발굴 방법에 대해서 스스로 고민해 보시길 추천해드립니다.


> **만약 Plotly, Pandas 문법이 어렵게 느껴지셨다면?**

- 우선 본 강의 핵심인 SQL 부터 순차적으로 복습하시는 것을 추천드립니다. 💪
- SQL을 충분히 이해하고 난 다음에는 꼭 Plotly나 Pandas를 사용하지 않으셔도 괜찮습니다.
- 스스로 분석 스토리 라인을 잡을 수 있고, 더 익숙한 툴이 있다면 SQL로 추출한 데이터를 해당 툴을 활용해서 문서화 하셔도 좋습니다.
- 다만, 본 강의에서 (Plotly, Pandas) 를 통한 리포팅 방법을 다룬 이유는
  - IT 기반의 서비스 회사 취업 희망시 Python 기반의 데이터 핸들링 역량이 큰 도움이 되고
  - Interactive 한 시각화 라이브러리는 현재 Plotly가 가장 우수하다고 판단되기 때문입니다.
- 반면 모든 시각화 자료를 Interactive 하게 만들 필요는 없으므로 상대적으로 학습 허들이 낮은 matplotlib이나 seaborn라이브러리를 함께 사용하시는것을 추천해 드립니다. 
